### Data parsing and analysis
- the suite of benchmarks is repeated at every interval of time
- a (micro)benchmark can be repeated multiple times
- a (micro)benchmark can have multiple setup
- the benchmark time is taken when the suite of benchmark is completed

In [47]:
import yaml
import requests
import matplotlib.pyplot as plt
import statistics as stat
import json
import datetime
import re
import pandas as pd
import numpy as np
import os
import plotly.graph_objects as go
from matplotlib.dates import DateFormatter

In [48]:
# set plot format
import matplotlib.pyplot as plt
%matplotlib inline
plt.rcParams["figure.figsize"] = (20,10)
cmap = plt.get_cmap('jet_r')
font = {'family' : 'DejaVu Sans',
        'weight' : 'normal',
        'size'   : 18}
plt.rc('font', **font)

In [49]:
# set date formatter
date_formatter = DateFormatter('%H:%M')

In [50]:
# helpers
def plot_dates(x, y, label=None, suptitle=None):
    fig, ax = plt.subplots()
    if suptitle:
        fig.suptitle(suptitle)
    ax.plot(x, y, label=label)
    ax.xaxis.set_major_formatter(date_formatter)
    fig.autofmt_xdate()
    plt.grid(True, linewidth=0.3, linestyle='-')
    plt.show()
    plt.close()
    
def plotly_dates(x, y, label=None, suptitle=None):
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=x, y=y, mode='lines', name=label))
    fig.update_layout(autosize=True)
    fig.update_yaxes(automargin=True)
    fig.show()

### Parsers Definition
Extract useful data from benchmarks outputs using regexps

In [51]:
def parser_sysbench(raw_data, print_errors=True):
    sys_res = []
    cpu_tests = [(r"events per second:\s*([0-9.]*)", "cpu: events per second", "events/s"),
                (r"avg:\s*([0-9.]*)", "cpu: avg latency", "ms")]
    fileio_tests = [(r"reads\/s:\s*([0-9.]*)", "fileio: fileop - read", "reads/s"),
                    (r"writes\/s:\s*([0-9.]*)", "fileio: fileop - write", "writes/s"),
                    (r"fsyncs\/s:\s*([0-9.]*)", "fileio: fileop - fsync", "fsyncs/s"),
                    (r"read, MiB\/s:\s*([0-9.]*)", "fileio: throughput - read", "MiB/s"),
                    (r"written, MiB\/s:\s*([0-9.]*)", "fileio: throughput - write", "MiB/s"),
                    (r"avg:\s*([0-9.]*)", "fileio: avg latency", "ms")]
    memory_tests = [(r"([0-9.,]*) per second", "memory: totalops per second", "ops/s"),
                    (r"([0-9.,]*) MiB\/sec", "memory: speed", "MiB/s"),
                    (r"avg:\s*([0-9.]*)", "memory: avg latency", "ms")]
    threads_tests = [(r"avg:\s*([0-9.]*)", "threads: avg latency", "ms")]
    for benchmark in [("cpu", cpu_tests), ("fileio", fileio_tests),
                      ("memory", memory_tests), ("threads", threads_tests)]:
        r_data = raw_data[benchmark[0]]
        tests = benchmark[1]
        for test in tests:
            match = re.findall(test[0], r_data, re.MULTILINE)
            res = float(match[0].replace(",", "."))
            name = test[1]
            unit = test[2]
            sys_res.append({"unit": unit, "value": res, "name": name})
    return sys_res

def parser_simplecpu(raw_data, print_errors=True):
    return [{"unit": "s", "value": raw_data, "name": "mean duration"}]

def parser_download(raw_data, print_errors=True):
    # extract size and time
    regex = r"Downloaded\s([0-9]*)[a-z\s]*([0-9.,]*)"
    match = re.findall(regex, raw_data, re.MULTILINE)
    size = float(match[0][0])/1000/1000
    time = float(match[0][1].replace(",", "."))
    return [{"unit": "MB/s", "value": round(size/time, 2), "name": "speed"}]

def parser_dd(raw_data, print_errors=True):
    # extract speed
    regex = r"s,\s([0-9.,]*)\s[a-zA-Z]*\/s"
    match = re.findall(regex, raw_data, re.MULTILINE)
    speed = float(str(match[0]).replace(",", "."))
    return [{"unit": "MB/s", "value": speed, "name": "speed"}]

def parser_web_benchmark(raw_data, print_errors=True):
    regex = r"Requests/sec:\s*([0-9.]*)"
    match = re.findall(regex, raw_data, re.MULTILINE)
    speed = float(str(match[0]).replace(",", "."))
    return [{"unit": "req/s", "value": speed, "name": "requests per second"}]

def parser_nench(raw_data, print_errors=True):
    # cpu
    try:
        cpu_res = []
        for cpu_test in ["SHA256", "bzip2", "AES"]:
            regex = re.escape(cpu_test) + ".*\n\s*([0-9,.]*) ([a-z]*)"
            match = re.findall(regex, raw_data, re.MULTILINE)
            res = float(str(match[0][0]).replace(",", "."))
            unit = str(match[0][1])
            cpu_res.append({"unit": unit, "value": res, "name": "cpu - " + cpu_test})
    except Exception as e:
        if print_errors:
            print("error: nench - cpu: " + str(e))
    # ioping
    try:
        ioping_res = []
        seekrate = (r"min\/avg\/max\/mdev = [0-9a-z.\s]*\/ ([0-9.]*) ([a-z]*)", "ioping: avg seek rate")
        srs = (r"generated.*iops. ([0-9.]*) (.*)", "ioping: sequential read speed")
        for ioping in [seekrate, srs]:
            regex = ioping[0]
            match = re.findall(regex, raw_data, re.MULTILINE)
            res = float(str(match[0][0]).replace(",", "."))
            unit = str(match[0][1])
            ioping_res.append({"unit": unit, "value": res, "name": ioping[1]})
    except Exception as e:
        if print_errors:
            print("error: nench - ioping: " + str(e))
        pass
    # dd
    try:
        dd_res = []
        regex = r"average:\s*([0-9.]*) ([a-zA-Z\/]*)$"
        match = re.findall(regex, raw_data, re.MULTILINE)
        res = float(str(match[0][0]).replace(",", "."))
        unit = str(match[0][1])
        dd_res.append({"unit": unit, "value": res, "name": "dd: avg sequential write speed"})
    except Exception as e:
        if print_errors:
            print("error: nench - dd: " + str(e))
    # speed test
    try:
        speed_res = []
        for speed_test in ["Cachefly CDN", "Leaseweb (NL)", "Softlayer DAL (US)", "Online.net (FR)", "OVH BHS (CA)"]:
            regex = re.escape(speed_test) + ":\s*([0-9.]*) ([a-zA-Z\/]*)"
            match = re.findall(regex, raw_data, re.MULTILINE)
            res = float(str(match[0][0]).replace(",", "."))
            unit = str(match[0][1])
            speed_res.append({"unit": unit, "value": res, "name": "net speed - " + speed_test})
    except Exception as e:
        if print_errors:
            print("error: nench - speed test: " + str(e))
    return cpu_res + ioping_res + dd_res + speed_res

def parser_aibenchmark(raw_data, print_errors=True):
    ai_res = []
    if raw_data["ai_score"]:
        ai_res.append({"unit": "score", "value": raw_data["ai_score"], "name": "ai score"})
    if raw_data["inference_score"]:
        ai_res.append({"unit": "score", "value": raw_data["inference_score"], "name": "inference score"})
    if raw_data["training_score"]:
        ai_res.append({"unit": "score", "value": raw_data["training_score"], "name": "training score"})
    return ai_res

### Apply parsers and extract data
For each benchmark extract a list of values (a benchmark can provide multiple extracted values, such as sysbench):
- extracted.name: is the name of the benchmark value extracted, e.g. cpu - SHA256
- extracted.value: is the extracted value, e.g. 3.279
- extracted.unit: extracted unit, e.g. seconds

In [52]:
benchmark_extractors = {"download": parser_download,
                        "dd": parser_dd,
                        "web-benchmark": parser_web_benchmark,
                        "nench-benchmark": parser_nench,
                        "sys-benchmark": parser_sysbench,
                        "simple-cpu": parser_simplecpu,
                        "ai-benchmark": parser_aibenchmark}


IGNORE_VMS_LIST = []


# get configuration
with open("config_benchmark_viewer.yml", 'r') as ymlfile:
    cfg = yaml.load(ymlfile, Loader=yaml.FullLoader)

# get data from the database
url = cfg["bin_database_url"] + "/all"
# print("getting data from: " + url)
response = requests.get(url=url)

data = response.json()
print("total VMs: %d\n\n" % len(data["bins"]))

# iter vms
for bin in data["bins"]:
    pars_err = 0
    id = bin["id"]
    if id in IGNORE_VMS_LIST:
        continue
    updated = bin["updated"]
    benchmarks = len(bin["values"])
    server = bin["values"][0]["server"]
    
    print(id)
    print(json.dumps(server, indent=2))
    
    # iters bench runs
    durations = []
    times = []
    results = {}
    for value in bin["values"]:
        durations.append(value["duration"])
        time = datetime.datetime.strptime(value["time"], '%Y-%m-%d %H:%M:%S.%f')
        times.append(time)
        
        # iter benchmarks
        for benchmark in value["benchmarks"]:
            if benchmark["name"] in benchmark_extractors.keys():
                try:
                    benchmark["extracted"] = benchmark_extractors[benchmark["name"]](benchmark["result"]["output"], print_errors=False)
                except Exception as e:
                    print("Error extracting: " + benchmark["name"] + " @ " + str(time) + "\n" + str(e))
                    pars_err += 1
    print("Parsing errors: " + str(pars_err))
        
    print("total benchmarks: %d\nupdated: %s\nduration (min, avg, max): %.2f, %.2f, %.2f"
          % (benchmarks, updated, min(durations), stat.mean(durations), max(durations)))
    
    plotly_dates(times, durations)
    print("\n\n")

# print(json.dumps(data, indent=2))

total VMs: 6


AWS_i-063baa2ee72c3ab33
{
  "hostname": "ip-172-31-28-51",
  "machine": "aarch64",
  "memory": "3.71 GB",
  "platform": "Linux-4.15.0-1063-aws-aarch64-with-Ubuntu-18.04-bionic",
  "processor": "aarch64",
  "username": "ubuntu",
  "version": "3.6.9 (default, Nov  7 2019, 10:44:02) \n[GCC 8.3.0]"
}
Error extracting: download @ 2020-04-02 13:31:42.405236
could not convert string to float: 
Error extracting: download @ 2020-04-02 13:31:42.405236
could not convert string to float: 
Parsing errors: 2
total benchmarks: 212
updated: 2020-04-10 10:10:43.690674
duration (min, avg, max): 596.29, 609.01, 1861.81





AWS_i-0733ddb8b1c753b35
{
  "hostname": "ip-172-31-23-249",
  "machine": "aarch64",
  "memory": "7.53 GB",
  "platform": "Linux-4.15.0-1063-aws-aarch64-with-Ubuntu-18.04-bionic",
  "processor": "aarch64",
  "username": "ubuntu",
  "version": "3.6.9 (default, Nov  7 2019, 10:44:02) \n[GCC 8.3.0]"
}
Parsing errors: 0
total benchmarks: 212
updated: 2020-04-10 10:10:45.927598
duration (min, avg, max): 600.04, 605.93, 625.03





AWS_i-0619c7938d65d53cf
{
  "hostname": "ip-172-31-14-58",
  "machine": "aarch64",
  "memory": "3.71 GB",
  "platform": "Linux-4.15.0-1063-aws-aarch64-with-Ubuntu-18.04-bionic",
  "processor": "aarch64",
  "username": "ubuntu",
  "version": "3.6.9 (default, Nov  7 2019, 10:44:02) \n[GCC 8.3.0]"
}
Parsing errors: 0
total benchmarks: 212
updated: 2020-04-10 10:10:42.068110
duration (min, avg, max): 596.89, 604.50, 637.56





AWS_i-0ef37f68caaf87f79
{
  "hostname": "ip-172-31-19-166",
  "machine": "x86_64",
  "memory": "15.38 GB",
  "platform": "Linux-4.15.0-1063-aws-x86_64-with-Ubuntu-18.04-bionic",
  "processor": "x86_64",
  "username": "ubuntu",
  "version": "3.6.9 (default, Nov  7 2019, 10:44:02) \n[GCC 8.3.0]"
}
Parsing errors: 0
total benchmarks: 212
updated: 2020-04-10 10:11:04.867354
duration (min, avg, max): 614.31, 630.19, 656.78





AWS_i-064f72b2f9a158570
{
  "hostname": "ip-172-31-4-207",
  "machine": "x86_64",
  "memory": "7.5 GB",
  "platform": "Linux-4.15.0-1063-aws-x86_64-with-Ubuntu-18.04-bionic",
  "processor": "x86_64",
  "username": "ubuntu",
  "version": "3.6.9 (default, Nov  7 2019, 10:44:02) \n[GCC 8.3.0]"
}
Error extracting: download @ 2020-04-02 13:18:46.835805
could not convert string to float: 
Error extracting: download @ 2020-04-02 13:18:46.835805
could not convert string to float: 
Parsing errors: 2
total benchmarks: 212
updated: 2020-04-10 10:11:08.823352
duration (min, avg, max): 625.53, 635.31, 1087.36





AWS_i-06f9bf39dcdbdfe05
{
  "hostname": "ip-172-31-20-192",
  "machine": "x86_64",
  "memory": "7.5 GB",
  "platform": "Linux-4.15.0-1063-aws-x86_64-with-Ubuntu-18.04-bionic",
  "processor": "x86_64",
  "username": "ubuntu",
  "version": "3.6.9 (default, Nov  7 2019, 10:44:02) \n[GCC 8.3.0]"
}
Parsing errors: 0
total benchmarks: 212
updated: 2020-04-10 10:11:11.671309
duration (min, avg, max): 625.65, 634.19, 696.72


## Data analysis
- use Pandas to analyze data
- preparare the data for Pandas: build a list where each entry is a benchmark value

In [53]:
rows = []
tests_uni = {}
# iter vms
for bin in data["bins"]:
    id = bin["id"]
    if id in IGNORE_VMS_LIST:
        continue
    updated = bin["updated"]
    server = bin["values"][0]["server"]
    
    # iters bench run
    for value in bin["values"]:
        duration = value["duration"]
        time = value["time"]
        
        # iter benchmarks
        for benchmark in value["benchmarks"]:
            if "extracted" not in benchmark:
                break
            extracted = benchmark["extracted"]
            
            for ext in extracted:
                test_id = hash(benchmark["name"] + str(benchmark["setup"]) + ext["name"])
                row = {"id": cfg["vms"][id.split("_", 1)[1]],
                       "duration": duration,
                       "time": pd.to_datetime(time, format='%Y-%m-%d %H:%M:%S.%f'),
                       "value": ext["value"],
                       "test_id": test_id}
                
                tests_uni[test_id] = {"bench_name": benchmark["name"],
                                      "setup": str(benchmark["setup"]),
                                      "extracted_name": ext["name"],
                                      "extracted_unit": ext["unit"]}
                        
                rows.append(row)           

#### Print the tests

In [54]:
print(json.dumps(tests_uni, indent=2))

{
  "-6470276688022354686": {
    "bench_name": "download",
    "setup": "{'url': 'https://speed.hetzner.de/1GB.bin'}",
    "extracted_name": "speed",
    "extracted_unit": "MB/s"
  },
  "-4455142584948155877": {
    "bench_name": "dd",
    "setup": "{'bs': '512', 'count': 1000}",
    "extracted_name": "speed",
    "extracted_unit": "MB/s"
  },
  "7940690598056476511": {
    "bench_name": "nench-benchmark",
    "setup": "{}",
    "extracted_name": "cpu - SHA256",
    "extracted_unit": "seconds"
  },
  "-4468568456060010188": {
    "bench_name": "nench-benchmark",
    "setup": "{}",
    "extracted_name": "cpu - bzip2",
    "extracted_unit": "seconds"
  },
  "8856277440634045623": {
    "bench_name": "nench-benchmark",
    "setup": "{}",
    "extracted_name": "cpu - AES",
    "extracted_unit": "seconds"
  },
  "-89371747706802877": {
    "bench_name": "nench-benchmark",
    "setup": "{}",
    "extracted_name": "dd: avg sequential write speed",
    "extracted_unit": "MiB/s"
  },
  "-44377

#### Print the dataset

In [55]:
print(len(rows))
# normalize the data
pd.set_option('display.max_rows', 20)
df = pd.json_normalize(rows)
df

119414


id    duration                       time  \
0       a1.large - eu-central-1b  604.652348 2020-04-01 12:10:44.370616   
1       a1.large - eu-central-1b  604.652348 2020-04-01 12:10:44.370616   
2       a1.large - eu-central-1b  604.652348 2020-04-01 12:10:44.370616   
3       a1.large - eu-central-1b  604.652348 2020-04-01 12:10:44.370616   
4       a1.large - eu-central-1b  604.652348 2020-04-01 12:10:44.370616   
...                          ...         ...                        ...   
119409  m5.large - eu-central-1b  629.940642 2020-04-10 07:11:10.660873   
119410  m5.large - eu-central-1b  629.940642 2020-04-10 07:11:10.660873   
119411  m5.large - eu-central-1b  629.940642 2020-04-10 07:11:10.660873   
119412  m5.large - eu-central-1b  629.940642 2020-04-10 07:11:10.660873   
119413  m5.large - eu-central-1b  629.940642 2020-04-10 07:11:10.660873   

          value              test_id  
0       184.790 -6470276688022354686  
1        52.900 -4455142584948155877  
2         3.152  7940690598056476511  
3         9.700 -4468568456060010188  
4         1.350  8856277440634045623  
...         ...                  ...  
119409  117.900 -5463033897504213318  
119410  111.920 -3798929868493560358  
119411   17.170 -2769959017664441581  
119412   17.150 -2769959017664441581  
119413  143.000 -3361628790205510285  

[119414 rows x 5 columns]

In [56]:
df.describe()

duration          value       test_id
count  119414.000000  119414.000000  1.194140e+05
mean      619.212581    2962.610386 -2.670605e+18
std        21.594446    9010.181315  4.636868e+18
min       596.288541       0.000000 -9.129838e+18
25%       603.060872       9.600000 -5.463034e+18
50%       624.957779      98.200000 -4.312169e+18
75%       631.460048     248.755000 -1.359152e+18
max      1861.812326   75922.080000  8.856277e+18

#### Print the extracted values for each benchmark with all the machines in a single graph
1. compute the mean for each benchmark for each machine grouping by: id, bench_name, setup, extracted.name, time
2. reset_index() to obtain a list of tuples
3. groupby bench_name, setup, extracted.name
4. plot for each group, grouping by id

In [57]:
pd.set_option('display.max_rows', 20)
gb = df.groupby(['id', 'test_id', 'time']).agg(
    {'value': ['mean']}).reset_index()
gb.columns = gb.columns.droplevel(1)
gb

id              test_id  \
0       a1.large - eu-central-1a -9129838053842969781   
1       a1.large - eu-central-1a -9129838053842969781   
2       a1.large - eu-central-1a -9129838053842969781   
3       a1.large - eu-central-1a -9129838053842969781   
4       a1.large - eu-central-1a -9129838053842969781   
...                          ...                  ...   
35594  m5.xlarge - eu-central-1b  8856277440634045623   
35595  m5.xlarge - eu-central-1b  8856277440634045623   
35596  m5.xlarge - eu-central-1b  8856277440634045623   
35597  m5.xlarge - eu-central-1b  8856277440634045623   
35598  m5.xlarge - eu-central-1b  8856277440634045623   

                            time        value  
0     2020-04-01 12:10:48.951110  2582.873333  
1     2020-04-01 13:10:41.285581  2568.546667  
2     2020-04-01 14:10:45.569354  2621.203333  
3     2020-04-01 15:10:47.208628  2597.200000  
4     2020-04-01 16:10:43.326671  2602.203333  
...                          ...          ...  
35594 2020-04-10 03:11:09.106718     0.964333  
35595 2020-04-10 04:11:09.378583     0.958667  
35596 2020-04-10 05:11:05.925726     0.971333  
35597 2020-04-10 06:11:04.781811     0.983667  
35598 2020-04-10 07:11:04.108610     0.961667  

[35599 rows x 4 columns]

In [58]:
pd.set_option('display.max_rows', None)
gbb = gb.groupby(['test_id'])
gbb.first() # print the first entry (can be many)

id                       time  \
test_id                                                                     
-9129838053842969781  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-8881728217457928557  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-7657539766404466826  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-6470276688022354686  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-6423626708498836163  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-6395710908068368376  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-5909743319740930821  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-5463033897504213318  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-5372501614743887625  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-4735622387902343944  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-4629900467098631001  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-4468568456060010188  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-4455142584948155877  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-4437783238973694805  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-4312168780494195145  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-3798929868493560358  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-3570249713550278748  m5.large - eu-central-1a 2020-04-01 12:11:11.813648   
-3361628790205510285  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-3114112425259084435  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-2769959017664441581  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-1359152175948454684  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
-89371747706802877    a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
 1523083029529004258  m5.large - eu-central-1a 2020-04-01 12:11:11.813648   
 1894491895297436432  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
 3662944213484690013  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
 4292027078976497100  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
 6902714533578967235  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
 7940690598056476511  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   
 8856277440634045623  a1.large - eu-central-1a 2020-04-01 12:10:48.951110   

                             value  
test_id                             
-9129838053842969781   2582.873333  
-8881728217457928557   1721.913333  
-7657539766404466826      0.100000  
-6470276688022354686    227.998000  
-6423626708498836163      9.856667  
-6395710908068368376      0.050000  
-5909743319740930821    146.886667  
-5463033897504213318    106.426667  
-5372501614743887625  21143.686667  
-4735622387902343944     40.356667  
-4629900467098631001  21143.686667  
-4468568456060010188      9.573667  
-4455142584948155877     44.840000  
-4437783238973694805     96.796667  
-4312168780494195145  37091.023333  
-3798929868493560358     98.454000  
-3570249713550278748    278.400000  
-3361628790205510285    170.800000  
-3114112425259084435     13.523333  
-2769959017664441581     11.906667  
-1359152175948454684      0.374532  
-89371747706802877      132.666667  
 1523083029529004258    150.600000  
 1894491895297436432   5508.900000  
 3662944213484690013      0.090000  
 4292027078976497100     26.906667  
 6902714533578967235    148.856667  
 7940690598056476511      3.159333  
 8856277440634045623      1.294333

In [59]:
for key, grp in gbb:
    print(tests_uni[key])
    fig = go.Figure()
    gbid = grp.groupby("id")
    for key2, grp2 in gbid:
        times = grp2["time"]
        values = grp2["value"]
        fig.add_trace(go.Scatter(x=times, y=values, mode='lines', name=key2))
    fig.update_layout(autosize=True)
    fig.update_yaxes(automargin=True)
    fig.show()

{'bench_name': 'sys-benchmark', 'setup': "{'cpu_max_prime': 2000, 'file_max_requests': 0, 'file_max_time': 60, 'file_test_mode': 'rndrw', 'file_total_size': '1GB', 'mem_block_size': '1M', 'mem_total_size': '10G', 'threads_max_time': 10, 'threads_num': 128}", 'extracted_name': 'fileio: fileop - read', 'extracted_unit': 'reads/s'}


{'bench_name': 'sys-benchmark', 'setup': "{'cpu_max_prime': 2000, 'file_max_requests': 0, 'file_max_time': 60, 'file_test_mode': 'rndrw', 'file_total_size': '1GB', 'mem_block_size': '1M', 'mem_total_size': '10G', 'threads_max_time': 10, 'threads_num': 128}", 'extracted_name': 'fileio: fileop - write', 'extracted_unit': 'writes/s'}


{'bench_name': 'sys-benchmark', 'setup': "{'cpu_max_prime': 2000, 'file_max_requests': 0, 'file_max_time': 60, 'file_test_mode': 'rndrw', 'file_total_size': '1GB', 'mem_block_size': '1M', 'mem_total_size': '10G', 'threads_max_time': 10, 'threads_num': 128}", 'extracted_name': 'fileio: avg latency', 'extracted_unit': 'ms'}


{'bench_name': 'download', 'setup': "{'url': 'https://speed.hetzner.de/1GB.bin'}", 'extracted_name': 'speed', 'extracted_unit': 'MB/s'}


{'bench_name': 'nench-benchmark', 'setup': '{}', 'extracted_name': 'net speed - Softlayer DAL (US)', 'extracted_unit': 'MiB/s'}


...

{'bench_name': 'sys-benchmark', 'setup': "{'cpu_max_prime': 2000, 'file_max_requests': 0, 'file_max_time': 60, 'file_test_mode': 'rndrw', 'file_total_size': '1GB', 'mem_block_size': '1M', 'mem_total_size': '10G', 'threads_max_time': 10, 'threads_num': 128}", 'extracted_name': 'memory: avg latency', 'extracted_unit': 'ms'}


{'bench_name': 'sys-benchmark', 'setup': "{'cpu_max_prime': 2000, 'file_max_requests': 0, 'file_max_time': 60, 'file_test_mode': 'rndrw', 'file_total_size': '1GB', 'mem_block_size': '1M', 'mem_total_size': '10G', 'threads_max_time': 10, 'threads_num': 128}", 'extracted_name': 'fileio: throughput - write', 'extracted_unit': 'MiB/s'}


{'bench_name': 'nench-benchmark', 'setup': '{}', 'extracted_name': 'net speed - Leaseweb (NL)', 'extracted_unit': 'MiB/s'}


{'bench_name': 'nench-benchmark', 'setup': '{}', 'extracted_name': 'cpu - SHA256', 'extracted_unit': 'seconds'}


{'bench_name': 'nench-benchmark', 'setup': '{}', 'extracted_name': 'cpu - AES', 'extracted_unit': 'seconds'}
